# Using Producer Mini-App

In [1]:
# System Libraries
import sys, os
sys.path.append("..")
import pandas as pd
import numpy as np
import ast
import pykafka
import mass.KafkaProducer


## logging
import logging
logging.basicConfig(level=logging.DEBUG)
logging.getLogger().setLevel(logging.ERROR)
logging.getLogger("py4j").setLevel(logging.ERROR)
 
# Pilot-Streaming
import pilot.streaming

import uuid
import time

/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/radical/utils/atfork/stdlib_fixer.py:72: UserWarning: logging handlers already registered.
  warnings.warn('logging handlers already registered.')


# 1. Benchmark Loop

In [2]:
for num_repeats in range(3):
    for num_producer_nodes in [1,2,4]:
        for num_broker_nodes in [1]:
    
            kafka_pilot_description1 = {
                "resource":"slurm+ssh://login1.wrangler.tacc.utexas.edu",
                "working_directory": os.path.join('/work/01131/tg804093/wrangler/', "work"),
                "number_cores": 48,
                "project": "TG-MCB090174",
                "queue": "normal",
                "walltime": 159,
                "type":"kafka"
            }
            kafka_pilot = pilot.streaming.PilotComputeService.create_pilot(kafka_pilot_description1)
            kafka_pilot.wait()
            
            dask_pilot_description = {
                "resource":"slurm+ssh://login1.wrangler.tacc.utexas.edu",
                "working_directory": os.path.join('/work/01131/tg804093/wrangler/', "work"),
                "number_cores": 48,
                "project": "TG-MCB090174",
                "queue": "normal",
                "walltime": 159,
                "type":"dask"
            }
            dask_pilot = pilot.streaming.PilotComputeService.create_pilot(dask_pilot_description)
            dask_pilot.wait()
            time.sleep(5)
            for number_parallel_tasks in [1, 2, 4, 8, 16, 24, 48]:
                run_id = str(uuid.uuid1())
                miniapp=mass.KafkaProducer.MiniApp(
                                               dask_scheduler=dask_pilot.get_details()['master_url'],
                                               kafka_zk_hosts=kafka_pilot.get_details()["master_url"],
                                               number_parallel_tasks=number_parallel_tasks,
                                               number_clusters=192,
                                               number_points_per_cluster=52084,
                                               number_points_per_message=5000,
                                               number_dim=3,
                                               number_produces=10,
                                               number_partitions=12,
                                               topic_name="test-"+run_id
                                              )
                miniapp.run()
            
            kafka_pilot.cancel()
            dask_pilot.cancel()

**** Job: 59726 State : Pending
look for configs in: /work/01131/tg804093/wrangler/work/kafka-3c5d2ebc-f88a-11e7-9064-549f3509766c/config
['broker-0']
Kafka Config: /work/01131/tg804093/wrangler/work/kafka-3c5d2ebc-f88a-11e7-9064-549f3509766c/config (Sat Jan 13 11:50:26 2018)
{'zookeeper.connection.timeout.ms': '6000', 'broker.id': '0', 'listeners': 'PLAINTEXT://c251-136:9092', 'zookeeper.connect': 'c251-136:2181'}
**** Job: 59727 State : Pending
Kafka: c251-136:2181, Dask: tcp://129.114.58.137:8786, Number Dask Nodes: 1,  Number Parallel Producers: 1
/home/01131/tg804093/work/kafka_2.11-1.0.0/bin/kafka-topics.sh --delete --zookeeper c251-136:2181 --topic Throughput
/home/01131/tg804093/work/kafka_2.11-1.0.0/bin/kafka-topics.sh --create --zookeeper c251-136:2181 --replication-factor 1 --partitions 12 --topic Throughput
/home/01131/tg804093/work/kafka_2.11-1.0.0/bin/kafka-topics.sh --describe --zookeeper c251-136:2181 --topic Throughput
Generate Block ID: 0
Waiting for Dask Tasks to com

distributed.client - WARNING - Client report stream closed to scheduler
distributed.client - WARNING - Client report stream closed to scheduler
tornado.application - ERROR - Exception in callback <functools.partial object at 0x2aaf7bf8ba48>
Traceback (most recent call last):
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/ioloop.py", line 605, in _run_callback
    ret = callback()
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/stack_context.py", line 277, in null_wrapper
    return fn(*args, **kwargs)
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/ioloop.py", line 626, in _discard_future_result
    future.result()
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/concurrent.py", line 238, in result
    raise_exc_info(self._exc_info)
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/gen.py", line 1063, in run
    yielded = self.gen.throw(*exc_info)
  File 

CancelledError: list-4b31a77f-345a-4697-8b19-0b68fb9cb369

tornado.application - ERROR - Exception in callback <functools.partial object at 0x2aaf8452ac58>
Traceback (most recent call last):
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/ioloop.py", line 605, in _run_callback
    ret = callback()
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/stack_context.py", line 277, in null_wrapper
    return fn(*args, **kwargs)
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/ioloop.py", line 626, in _discard_future_result
    future.result()
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/concurrent.py", line 238, in result
    raise_exc_info(self._exc_info)
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/tornado/gen.py", line 1063, in run
    yielded = self.gen.throw(*exc_info)
  File "/home/01131/tg804093/anaconda2/lib/python2.7/site-packages/distributed/client.py", line 804, in _update_scheduler_info
    self._scheduler_iden

# 2. Mini App Test

Check Kafka Broker

In [3]:
client = pykafka.KafkaClient(zookeeper_hosts=kafka_details["master_url"])
topic = client.topics['test']
producer = topic.get_sync_producer()
consumer = topic.get_simple_consumer()

In [4]:
count = 0
number_total_points = 0
number_dimensions = 0
for i in range(100):
    message = consumer.consume(block=False)
    if message is not None:
        data_np = np.array(ast.literal_eval(message.value))
        num_points = data_np.shape[0]
        number_dimensions = data_np.shape[1]
        count =  count + 1
        number_total_points = number_total_points + num_points
    #print "Consumed message: %d, Number Points: %d, Number Dimensions: %d"%\
    #        (count, num_points, number_dimensions)   
        
print("Total Messages: %d, Total Points: %d, Number Dimensions: %d"%(count, number_total_points, number_dimensions))

Total Messages: 100, Total Points: 100000, Number Dimensions: 3
